In [1]:
import requests
import pandas as pd
import numpy as np

http_proxy  = "http://proxy-web.micron.com:80"
https_proxy = "http://proxy-web.micron.com:80"
proxyDict = { 
    "http":http_proxy, 
    "https":https_proxy              
}

pd.set_option('display.max_rows', None) #show every row for pandas
pd.set_option('display.max_columns', None) #show every column for pandas

g_year = 108
g_season = 1
g_how_many_year = 3

In [2]:
# sii:上市, otc:上櫃
# TWSE之數據是至該季的累計數據而非單季數據, EX: Q3=> TWSE: Q1~Q3, 財報狗:Q3
def financial_statement(year, season, stocktype, type='綜合損益彙總表'):
    if year >= 1000:
        year -= 1911
        
    if type == '綜合損益彙總表':
        url = 'https://mops.twse.com.tw/mops/web/ajax_t163sb04'
    elif type == '資產負債彙總表':
        url = 'https://mops.twse.com.tw/mops/web/ajax_t163sb05'
    elif type == '營益分析彙總表':
        url = 'https://mops.twse.com.tw/mops/web/ajax_t163sb06'
    else:
        print('type does not match')
    
    r = requests.post(url, {
        'encodeURIComponent':1,
        'step':1,
        'firstin':1,
        'off':1,
        'TYPEK':stocktype,
        'year':str(year),
        'season':str(season),
    }, stream=True)#, verify=False, proxies=proxyDict)
    
    r.encoding = 'utf8'
    dfs = pd.read_html(r.text)
    
    
    for i, df in enumerate(dfs):
        df.columns = df.iloc[0]
        dfs[i] = df.iloc[1:]
        
    df = pd.concat(dfs).applymap(lambda x: x if x != '--' else np.nan)
    df = df[df[u'公司代號'] != u'公司代號']
    df = df[~df[u'公司代號'].isnull()]
    
    #http://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.add_suffix.html
    #http://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.add_prefix.html
    suffix_format = "_{0}Q{1}".format(year, season)
    
    #return df.add_suffix(suffix_format)
    return df

In [3]:
def generate_df_for_stocktype(year, season, howmany_year_data, stocktype, title_name, with_col_name, sheettype):
    df = financial_statement(year, season, stocktype, type=sheettype)[[u'公司代號',u'公司名稱',with_col_name]]
    df.rename(columns = {df.columns[2]: '{0}(%)_{1}Q{2}'.format(title_name, year, season)}, inplace = True)

    for i in range(howmany_year_data*4):
        # calculate previous quarter data 107Q1 => we want the previous data is 106Q4 AND then 106Q3, 106Q2, 106Q1, 105Q4
        if (season != 1):
            season = season - 1
        else:
            season = 4
            year = year - 1
        #https://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.merge.html
        dfanother = financial_statement(year, season, stocktype, type=sheettype)[[u'公司代號',with_col_name]]    
        print(dfanother.columns[1])

        dfanother.rename(columns = {dfanother.columns[1]: '{0}(%)_{1}Q{2}'.format(title_name, year, season)}, inplace = True)

        df = df.merge(dfanother, on=u'公司代號', how='inner')
        print("year:", year)
        #print("year: {0}".format(year))
        print("season:", season)
        #print("season: {0}".format(season))

    return df

In [4]:
df_operating_profit_sii = generate_df_for_stocktype(g_year, g_season, g_how_many_year, 'sii', 'OperationProfit', u'營業利益率(%)(營業利益)/(營業收入)', '營益分析彙總表')

df_operating_profit_sii

C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:34: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



營業利益率(%)(營業利益)/(營業收入)
('year:', 107)
('season:', 4)
營業利益率(%)(營業利益)/(營業收入)
('year:', 107)
('season:', 3)
營業利益率(%)(營業利益)/(營業收入)
('year:', 107)
('season:', 2)
營業利益率(%)(營業利益)/(營業收入)
('year:', 107)
('season:', 1)
營業利益率(%)(營業利益)/(營業收入)
('year:', 106)
('season:', 4)
營業利益率(%)(營業利益)/(營業收入)
('year:', 106)
('season:', 3)
營業利益率(%)(營業利益)/(營業收入)
('year:', 106)
('season:', 2)
營業利益率(%)(營業利益)/(營業收入)
('year:', 106)
('season:', 1)
營業利益率(%)(營業利益)/(營業收入)
('year:', 105)
('season:', 4)
營業利益率(%)(營業利益)/(營業收入)
('year:', 105)
('season:', 3)
營業利益率(%)(營業利益)/(營業收入)
('year:', 105)
('season:', 2)
營業利益率(%)(營業利益)/(營業收入)
('year:', 105)
('season:', 1)


公司代號      公司名稱 OperationProfit(%)_108Q1 OperationProfit(%)_107Q4  \
0    1101        台泥                    19.85                    22.62   
1    1102        亞泥                    19.49                    21.94   
2    1103        嘉泥                   -12.37                    -4.95   
3    1104      環球水泥                     0.85                     3.82   
4    1108      幸福水泥                    -3.16                    -4.66   
5    1109      信大水泥                    20.90                    26.19   
6    1110        東泥                     3.51                     2.42   
7    1201      味全公司                    -0.32                     2.64   
8    1203      味王公司                    14.77                    16.06   
9    1210      大成長城                     3.71                     3.14   
10   1215      卜蜂企業                     6.70                     6.05   
11   1216        統一                     6.97                     6.25   
12   1217       愛之味                     2.32                     1.55   
13   1218      泰山企業                     1.98                     1.14   
14   1219      福壽實業                     0.64                    -0.71   
15   1220        台榮                     2.21                     4.02   
16   1225       福懋油                     4.02                     3.04   
17   1227        佳格                    13.81                    11.52   
18   1229      聯華實業                     5.55                     5.89   
19   1231      聯華食品                     4.79                     7.64   
20   1232       大統益                     8.89                     6.56   
21   1233        天仁                     9.72                     7.50   
22   1234        黑松                     1.73                     2.51   
23   1235        興泰                   -85.37                     9.82   
24   1236      宏亞食品                     1.50                     0.34   
25   1256   鮮活果汁-KY                    16.56                    18.76   
26   1262     綠悅-KY                   -14.76                   -10.43   
27   1301        台塑                     9.94                    11.00   
28   1303      南亞塑膠                     3.21                     8.83   
29   1304        台聚                     4.51                     3.17   
30   1305        華夏                     5.69                    10.35   
31   1307      三芳化工                     5.26                     4.01   
32   1308        亞聚                     6.96                     1.13   
33   1309      台達化工                     4.56                     1.28   
34   1310        台苯                    11.80                     9.98   
35   1312      國喬石化                     7.47                    11.07   
36   1313        聯成                    -1.40                     1.76   
37   1314       中石化                    -1.75                     7.99   
38   1315      達新工業                    -1.06                    -0.35   
39   1316        上曜                   -43.44                     7.61   
40   1319        東陽                    10.12                     8.04   
41   1321        大洋                    -2.38                    -3.25   
42   1323        永裕                    10.74                    12.58   
43   1324      地球工業                    -1.39                     0.14   
44   1325        恒大                     5.02                     5.34   
45   1326        台化                     9.39                     9.40   
46   1337     再生-KY                   -54.23                  -124.27   
47   1338     廣華-KY                     6.28                     8.65   
48   1339        昭輝                    13.34                    13.55   
49   1340     勝悅-KY                   -15.66                     6.14   
50   1402       遠東新                     5.55                     6.47   
51   1410        南染                    16.00                    23.59   
52   1413      宏洲纖維                     3.45                     5.44   
53   1414        東和                    -6.88                   

In [5]:
df_operating_profit_otc = generate_df_for_stocktype(g_year, g_season, g_how_many_year, 'otc', 'OperationProfit', u'營業利益率(%)(營業利益)/(營業收入)', '營益分析彙總表')

df_operating_profit_otc

C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:34: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



營業利益率(%)(營業利益)/(營業收入)
('year:', 107)
('season:', 4)
營業利益率(%)(營業利益)/(營業收入)
('year:', 107)
('season:', 3)
營業利益率(%)(營業利益)/(營業收入)
('year:', 107)
('season:', 2)
營業利益率(%)(營業利益)/(營業收入)
('year:', 107)
('season:', 1)
營業利益率(%)(營業利益)/(營業收入)
('year:', 106)
('season:', 4)
營業利益率(%)(營業利益)/(營業收入)
('year:', 106)
('season:', 3)
營業利益率(%)(營業利益)/(營業收入)
('year:', 106)
('season:', 2)
營業利益率(%)(營業利益)/(營業收入)
('year:', 106)
('season:', 1)
營業利益率(%)(營業利益)/(營業收入)
('year:', 105)
('season:', 4)
營業利益率(%)(營業利益)/(營業收入)
('year:', 105)
('season:', 3)
營業利益率(%)(營業利益)/(營業收入)
('year:', 105)
('season:', 2)
營業利益率(%)(營業利益)/(營業收入)
('year:', 105)
('season:', 1)


公司代號    公司名稱 OperationProfit(%)_108Q1 OperationProfit(%)_107Q4  \
0    1258   其祥-KY                    -0.40                    -2.87   
1    1259      安心                     2.15                     3.19   
2    1264      德麥                    16.46                    17.44   
3    1333     恩得利                    -3.00                   -33.04   
4    1336      台翰                     2.55                     6.02   
5    1565    精華光學                    29.03                    30.09   
6    1566      捷邦                     4.13                     3.05   
7    1569      濱川                     4.29                     5.81   
8    1570    力肯實業                     8.14                    14.24   
9    1580    新麥企業                    12.97                    15.24   
10   1584    精剛精密                    -5.38                   -11.09   
11   1586    和勤精機                    -6.30                     6.85   
12   1591   駿吉-KY                     3.71                     6.65   
13   1593      祺驊                    12.51                    14.82   
14   1595    川寶科技                     2.44                    12.26   
15   1597      直得                    17.28                    29.10   
16   1599     宏佳騰                     9.94                     8.76   
17   1742      台蠟                     7.68                   -17.75   
18   1752      南光                     8.78                     8.24   
19   1777      生泰                    22.69                    19.05   
20   1781    合世生醫                   -19.24                    -9.24   
21   1784    訊聯生技                     6.66                     4.44   
22   1785     光洋科                     7.28                     3.56   
23   1787     福盈科                     7.00                     8.05   
24   1788    杏昌生技                     9.44                     9.52   
25   1795    美時製藥                    20.43                     6.98   
26   1799      易威                   -64.80                   -56.20   
27   1813     寶利徠                     3.50                    -7.09   
28   1815    富喬工業                     7.87                    14.03   
29   2035    唐榮公司                    -4.42                    -9.36   
30   2061      風青                    -0.98                    -0.46   
31   2063      世鎧                    20.08                    19.51   
32   2064      晉椿                    -3.61                     2.68   
33   2066      世德                     7.92                     5.22   
34   2067      嘉鋼                    -5.36                     5.20   
35   2221    大甲永和                    15.29                    15.98   
36   2230      泰茂                    -2.55                     2.16   
37   2233      宇隆                    17.89                    20.54   
38   2235      謚源                    16.56                    12.44   
39   2596    綠意開發                 -1469.54                    33.25   
40   2640     大車隊                    20.09                    15.99   
41   2641    正德海運                    19.59                    18.57   
42   2643      捷迅                     3.35                     3.33   
43   2718      晶悅                     3.18                    -7.48   
44   2719     燦星旅                    -6.85                    -4.64   
45   2724   富驛-KY                   -18.99                   -18.39   
46   2726   雅茗-KY                    10.41                     6.43   
47   2729    瓦城泰統                    11.41                    10.23   
48   2732    六角國際                    10.69                     7.37   
49   2734     易飛網                    -6.56                    -7.93   
50   2736      高野                     9.91                    -5.57   
51   2740      天蔥                   -51.19                   -20.38   
52   2916    滿心企業                     2.42                     7.28   
53   2924   東凌-KY                   -17.58                   -16.01   
54   2926    誠品生活                    10.42                     6.09   
55   2928   紅馬-KY            

In [6]:
#Database-style DataFrame joining/merging: join, merge
#Concatenating objects: concat, append

#ignore_index = True 可以忽略合併時舊的 index 欄位，改採用自動產生的 index
df_operating_profit = pd.concat([df_operating_profit_sii,df_operating_profit_otc],axis=0, ignore_index=True)

df_operating_profit

公司代號      公司名稱 OperationProfit(%)_108Q1 OperationProfit(%)_107Q4  \
0     1101        台泥                    19.85                    22.62   
1     1102        亞泥                    19.49                    21.94   
2     1103        嘉泥                   -12.37                    -4.95   
3     1104      環球水泥                     0.85                     3.82   
4     1108      幸福水泥                    -3.16                    -4.66   
5     1109      信大水泥                    20.90                    26.19   
6     1110        東泥                     3.51                     2.42   
7     1201      味全公司                    -0.32                     2.64   
8     1203      味王公司                    14.77                    16.06   
9     1210      大成長城                     3.71                     3.14   
10    1215      卜蜂企業                     6.70                     6.05   
11    1216        統一                     6.97                     6.25   
12    1217       愛之味                     2.32                     1.55   
13    1218      泰山企業                     1.98                     1.14   
14    1219      福壽實業                     0.64                    -0.71   
15    1220        台榮                     2.21                     4.02   
16    1225       福懋油                     4.02                     3.04   
17    1227        佳格                    13.81                    11.52   
18    1229      聯華實業                     5.55                     5.89   
19    1231      聯華食品                     4.79                     7.64   
20    1232       大統益                     8.89                     6.56   
21    1233        天仁                     9.72                     7.50   
22    1234        黑松                     1.73                     2.51   
23    1235        興泰                   -85.37                     9.82   
24    1236      宏亞食品                     1.50                     0.34   
25    1256   鮮活果汁-KY                    16.56                    18.76   
26    1262     綠悅-KY                   -14.76                   -10.43   
27    1301        台塑                     9.94                    11.00   
28    1303      南亞塑膠                     3.21                     8.83   
29    1304        台聚                     4.51                     3.17   
30    1305        華夏                     5.69                    10.35   
31    1307      三芳化工                     5.26                     4.01   
32    1308        亞聚                     6.96                     1.13   
33    1309      台達化工                     4.56                     1.28   
34    1310        台苯                    11.80                     9.98   
35    1312      國喬石化                     7.47                    11.07   
36    1313        聯成                    -1.40                     1.76   
37    1314       中石化                    -1.75                     7.99   
38    1315      達新工業                    -1.06                    -0.35   
39    1316        上曜                   -43.44                     7.61   
40    1319        東陽                    10.12                     8.04   
41    1321        大洋                    -2.38                    -3.25   
42    1323        永裕                    10.74                    12.58   
43    1324      地球工業                    -1.39                     0.14   
44    1325        恒大                     5.02                     5.34   
45    1326        台化                     9.39                     9.40   
46    1337     再生-KY                   -54.23                  -124.27   
47    1338     廣華-KY                     6.28                     8.65   
48    1339        昭輝                    13.34                    13.55   
49    1340     勝悅-KY                   -15.66                     6.14   
50    1402       遠東新                     5.55                     6.47   
51    1410        南染                    16.00                    23.59   
52    1413      宏洲纖維                     3.45                     5.44   
53    1414

In [7]:
#檢查column資料型態

#df_operating_profit.info() #non-null object
#df_operating_profit.dtypes #object
#df_operating_profit.applymap(np.isreal) #all False
'''
公司代號              int64
公司名稱             object
OperationProfit(%)_107Q1    float64
OperationProfit(%)_106Q4    float64
OperationProfit(%)_106Q3    float64
OperationProfit(%)_106Q2    float64
OperationProfit(%)_106Q1    float64
OperationProfit(%)_105Q4    float64
OperationProfit(%)_105Q3    float64
OperationProfit(%)_105Q2    float64
OperationProfit(%)_105Q1    float64
OperationProfit(%)_104Q4    float64
OperationProfit(%)_104Q3    float64
OperationProfit(%)_104Q2    float64
OperationProfit(%)_104Q1    float64
dtype: object
'''

df_operating_profit = df_operating_profit.convert_objects(convert_numeric=True) #轉成float型態方便後續處理

df_operating_profit.convert_objects(convert_numeric=True).dtypes #轉成float型態方便後續處理

C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:25: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:27: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.


公司代號                          int64
公司名稱                         object
OperationProfit(%)_108Q1    float64
OperationProfit(%)_107Q4    float64
OperationProfit(%)_107Q3    float64
OperationProfit(%)_107Q2    float64
OperationProfit(%)_107Q1    float64
OperationProfit(%)_106Q4    float64
OperationProfit(%)_106Q3    float64
OperationProfit(%)_106Q2    float64
OperationProfit(%)_106Q1    float64
OperationProfit(%)_105Q4    float64
OperationProfit(%)_105Q3    float64
OperationProfit(%)_105Q2    float64
OperationProfit(%)_105Q1    float64
dtype: object

In [8]:
def isFloat(element):  
    try:
        float(element)
        return True
    except ValueError:
        return False

In [9]:
def growth_func(row, year, season):
    previous_year = year - 1
    #判斷是否為文字而非數字
    if(isFloat(row['OperationProfit(%)_{0}Q{1}'.format(year, season)]) == True):
        subsequent_value = float(row['OperationProfit(%)_{0}Q{1}'.format(year, season)])
        previous_value = float(row['OperationProfit(%)_{0}Q{1}'.format(previous_year, season)])
   
        if(previous_value == 0):
            result = ((subsequent_value - previous_value)/np.abs(subsequent_value))*100
        else:
            result = ((subsequent_value - previous_value)/np.abs(previous_value))*100            
        return float("{0:.2f}".format(result)) # Limiting floats to two decimal points
     
    else:
        return 'NoValue'

In [10]:
def ma2q_growth_func(row, year, season):
    #判斷是否為文字而非數字
    if(isFloat(row['OperationProfit(%)_{0}Q{1}'.format(year, season)]) == True):
        previous_value = float(row['Growth_{0}Q{1}'.format(year, season)])
        if (season != 1):
            season = season - 1
        else:
            season = 4
            year = year - 1
        subsequent_value = float(row['Growth_{0}Q{1}'.format(year, season)])
        
        result = ((subsequent_value + previous_value)/2)
        return float("{0:.2f}".format(result)) # Limiting floats to two decimal points
    
    else:
        return 'NoValue'

In [11]:
# use the apply function in pandas to apply the function
# Note the axis=1 specifier, that means that the application is done at a row, rather than a column level
# df_eps.apply (lambda row: growth_func (row),axis=1)

year = g_year
season = g_season
howmany_year_data = g_how_many_year

#first 4 quarter don't need to be calculated growth
for i in range(int(howmany_year_data*4-4)):
    df_operating_profit['Growth_{0}Q{1}'.format(year, season)] = df_operating_profit.apply (lambda row: growth_func(row, year, season),axis=1)
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

In [12]:
# use the apply function in pandas to apply the function
# Note the axis=1 specifier, that means that the application is done at a row, rather than a column level
# df_eps.apply (lambda row: growth_func (row),axis=1)

year = g_year
season = g_season
howmany_year_data = g_how_many_year

#first 4 quarter don't need to be calculated growth
for i in range(int(howmany_year_data*4-4-1)):
    df_operating_profit['2QMAGrowth_{0}Q{1}'.format(year, season)] = df_operating_profit.apply (lambda row: ma2q_growth_func(row, year, season),axis=1)
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

In [13]:
def get_basic_info_for_ftock(stocktype):

    #get basic info of company
    '''
    抓取上市櫃股票的代號、名稱...等資料。
    上市
    http://isin.twse.com.tw/isin/C_public.jsp?strMode=2
    上櫃
    http://isin.twse.com.tw/isin/C_public.jsp?strMode=4
    '''
    #http://bloggerkaiweng.blogspot.com/2016/09/python.html

    if(stocktype == 'sii'):
        url='http://isin.twse.com.tw/isin/C_public.jsp?strMode=2'
    else:
        url='http://isin.twse.com.tw/isin/C_public.jsp?strMode=4'
    
    r = requests.get(url, stream=True)#, verify=False, proxies=proxyDict)
    r.encoding = 'big5hkscs' 
    dfshow = pd.read_html(r.text)

    for i, df in enumerate(dfshow):
        df.columns = df.iloc[0]
        dfshow[i] = df.iloc[1:]

    df = pd.concat(dfshow).applymap(lambda x: x if x != '--' else np.nan)
    df = df[df[u'有價證券代號及名稱'] != u'股票']
    df = df[~df[u'有價證券代號及名稱'].isnull()]
    df = df.reset_index(drop=True)
    
    newdf=df[df[u'產業別'] > '0']
    del newdf[u'國際證券辨識號碼(ISIN Code)'],newdf['CFICode'],newdf[u'備註']

    df2=newdf[u'有價證券代號及名稱'].str.split(u' ', expand=True)
    df2 = df2.reset_index(drop=True)
    newdf = newdf.reset_index(drop=True)
    for i in df2.index:
        if u'　' in df2.iat[i,0]:
            df2.iat[i,1]=df2.iat[i,0].split(u'　')[1]
            df2.iat[i,0]=df2.iat[i,0].split(u'　')[0]
    newdf=df2.join(newdf)
    newdf=newdf.rename(columns = {0:u'公司代號',1:u'股票名稱'})
    del newdf[u'有價證券代號及名稱']

    return newdf

In [14]:
df_basicinfo_sii = get_basic_info_for_ftock('sii').convert_objects(convert_numeric=True) #轉成float型態
df_basicinfo_otc = get_basic_info_for_ftock('otc').convert_objects(convert_numeric=True) #轉成float型態

df_basicinfo = pd.concat([df_basicinfo_sii,df_basicinfo_otc],axis=0, ignore_index=True)
#df_eps_basicinfo_sii.dtypes
#df_eps_basicinfo_otc

df_operating_profit = df_operating_profit.merge(df_basicinfo, on=u'公司代號', how='inner')

df_operating_profit

C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:1: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
  """Entry point for launching an IPython kernel.
C:\ProgramData\Anaconda2\lib\site-packages\ipykernel_launcher.py:2: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
  


公司代號      公司名稱  OperationProfit(%)_108Q1  OperationProfit(%)_107Q4  \
0     1101        台泥                     19.85                     22.62   
1     1102        亞泥                     19.49                     21.94   
2     1103        嘉泥                    -12.37                     -4.95   
3     1104      環球水泥                      0.85                      3.82   
4     1108      幸福水泥                     -3.16                     -4.66   
5     1109      信大水泥                     20.90                     26.19   
6     1110        東泥                      3.51                      2.42   
7     1201      味全公司                     -0.32                      2.64   
8     1203      味王公司                     14.77                     16.06   
9     1210      大成長城                      3.71                      3.14   
10    1215      卜蜂企業                      6.70                      6.05   
11    1216        統一                      6.97                      6.25   
12    1217       愛之味                      2.32                      1.55   
13    1218      泰山企業                      1.98                      1.14   
14    1219      福壽實業                      0.64                     -0.71   
15    1220        台榮                      2.21                      4.02   
16    1225       福懋油                      4.02                      3.04   
17    1227        佳格                     13.81                     11.52   
18    1229      聯華實業                      5.55                      5.89   
19    1231      聯華食品                      4.79                      7.64   
20    1232       大統益                      8.89                      6.56   
21    1233        天仁                      9.72                      7.50   
22    1234        黑松                      1.73                      2.51   
23    1235        興泰                    -85.37                      9.82   
24    1236      宏亞食品                      1.50                      0.34   
25    1256   鮮活果汁-KY                     16.56                     18.76   
26    1262     綠悅-KY                    -14.76                    -10.43   
27    1301        台塑                      9.94                     11.00   
28    1303      南亞塑膠                      3.21                      8.83   
29    1304        台聚                      4.51                      3.17   
30    1305        華夏                      5.69                     10.35   
31    1307      三芳化工                      5.26                      4.01   
32    1308        亞聚                      6.96                      1.13   
33    1309      台達化工                      4.56                      1.28   
34    1310        台苯                     11.80                      9.98   
35    1312      國喬石化                      7.47                     11.07   
36    1313        聯成                     -1.40                      1.76   
37    1314       中石化                     -1.75                      7.99   
38    1315      達新工業                     -1.06                     -0.35   
39    1316        上曜                    -43.44                      7.61   
40    1319        東陽                     10.12                      8.04   
41    1321        大洋                     -2.38                     -3.25   
42    1323        永裕                     10.74                     12.58   
43    1324      地球工業                     -1.39                      0.14   
44    1325        恒大                      5.02                      5.34   
45    1326        台化                      9.39                      9.40   
46    1337     再生-KY                    -54.23                   -124.27   
47    1338     廣華-KY                      6.28                      8.65   
48    1339        昭輝                     13.34                     13.55   
49    1340     勝悅-KY                    -15.66                      6.14   
50    1402       遠東新                      5.55                      6.47   
51    1410        南染                     16.00        

In [15]:
# pandas styling
def color_white(val):
    """
    Takes a scalar and returns a string with
    the css property `'color: red'` for negative
    strings, black otherwise.
    """
    color = 'white'
    return 'color: %s' % color

def background_color(val):    
    if float(val) < 0:
        backgroundcolor = '#ff0000'
    elif float(val) < 10:
        backgroundcolor = '#f47721'
    elif float(val) < 20:
        backgroundcolor = '#ffdd00'
    elif float(val) < 30:
        backgroundcolor = '#5ecc62'
    else:
        backgroundcolor = '#00ad45'
    return 'background-color: %s' % backgroundcolor

"""
Export to Excel
Some support is available for exporting styled DataFrames to Excel worksheets using the OpenPyXL or XlsxWriter engines. 
CSS2.2 properties handled include:

* background-color
* border-style, border-width, border-color and their {top, right, bottom, left variants}
* color
* font-family
* font-style
* font-weight
* text-align
* text-decoration
* vertical-align
* white-space: nowrap
"""
def font_family(val):    
    fontfamily = 'Calibri'
    return 'font-family: %s' % fontfamily

def font_size(val):    
    fontsize = '10pt'
    return 'font-size: %s' % fontsize

In [16]:
# styled dataframe can use .to_excel('Styled_Basic_EPS.xlsx', engine='openpyxl') to export excel with style
year = g_year
season = g_season
howmany_year_data = g_how_many_year

#first 4 quarter don't need to be calculated growth
columns_name = []
for i in range(int(howmany_year_data*4-4)):
    columns_name.append('Growth_{0}Q{1}'.format(year, season))
    columns_name.append('2QMAGrowth_{0}Q{1}'.format(year, season))
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

print(columns_name)
# the cell’s style depends only on it’s own value. That means we should use the Styler.applymap method which works elementwise.
# Now suppose you wanted to highlight the maximum value in each column. We can’t use .applymap anymore since that operated elementwise. Instead, we’ll turn to .apply which operates columnwise (or rowwise using the axis keyword).
#df_eps.style.applymap(color_negative_red, subset=pd.IndexSlice[:, ['Growth_107Q1','Growth_106Q4','Growth_106Q3','Growth_106Q2','Growth_106Q1','Growth_105Q4','Growth_105Q3','Growth_105Q2']]).applymap(background_color, subset=pd.IndexSlice[:, ['Growth_107Q1','Growth_106Q4','Growth_106Q3','Growth_106Q2','Growth_106Q1','Growth_105Q4','Growth_105Q3','Growth_105Q2']]).to_excel('Styled_Basic_EPS.xlsx', 'EPS_Basic', engine='openpyxl')
df_operating_profit.style.applymap(color_white, subset=pd.IndexSlice[:, columns_name]).applymap(background_color, subset=pd.IndexSlice[:, columns_name]).applymap(font_family).applymap(font_size).to_excel('Styled_Basic_Perspective_OperationProfit.xlsx', 'OperationProfit_Basic', engine='openpyxl')

# Pandas style function to hignlight specific columns
# http://pandas.pydata.org/pandas-docs/stable/style.html#Finer-Control:-Slicing
# Finer Control: Slicing
# ex: df.style.apply(highlight_max, subset=['B', 'C', 'D'])

['Growth_108Q1', '2QMAGrowth_108Q1', 'Growth_107Q4', '2QMAGrowth_107Q4', 'Growth_107Q3', '2QMAGrowth_107Q3', 'Growth_107Q2', '2QMAGrowth_107Q2', 'Growth_107Q1', '2QMAGrowth_107Q1', 'Growth_106Q4', '2QMAGrowth_106Q4', 'Growth_106Q3', '2QMAGrowth_106Q3', 'Growth_106Q2', '2QMAGrowth_106Q2']


C:\ProgramData\Anaconda2\lib\site-packages\pandas\core\indexing.py:1472: FutureWarning: 
Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/indexing.html#deprecate-loc-reindex-listlike
  return self._getitem_tuple(key)
